In [1]:
import itertools
import numpy as np
import pandas as pd
from sklearn.preprocessing import LabelEncoder

## Preprocess

In [2]:
posts = pd.read_csv('csvs/Posts.csv')
posts.dropna(subset=['Body', 'OwnerUserId'], how='any', inplace=True)

# Shuffle
posts = posts.sample(frac=1, random_state=42, replace=False, ignore_index=True)

questions = posts[posts['PostTypeId']==1]
answers = posts[posts['PostTypeId']==2]

print('Question Counts', len(questions))
print('Answers Counts', len(answers))
questions.head()

Question Counts 210226
Answers Counts 206435


Id                                              Title  \
0  437734  Effect of sex at specific point with confidenc...   
1  622877              Poisson process for small sample size   
5  517792  Did I correctly apply the factorisation theore...   
6  344644  IBM SPSS Damped Trend time series analysis met...   
7  620838  Mixed model development for repeated measures ...   

                                                Body  \
0  &lt;p&gt;Assume I model PEFR (related to lung ...   
1  &lt;p&gt;Suppose I have a data set that contai...   
5  &lt;p&gt;Suppose that we have a density &lt;sp...   
6  &lt;p&gt;I have been doing a time series analy...   
7  &lt;p&gt;I have longitudinal data for multiple...   

                                                Tags  PostTypeId  \
0                 |r|regression|confidence-interval|           1   
1  |regression|poisson-distribution|poisson-proce...           1   
5  |probability|estimation|inference|estimators|s...           1   
6                           |time-series|spss|trend|           1   
7  |mixed-model|lme4-nlme|repeated-measures|multi...           1   

              CreationDate  OwnerUserId  ParentId  
0  2019-11-24T19:50:42.807       266724       NaN  
1  2023-08-01T15:57:49.950       314344       NaN  
5  2021-04-01T18:01:50.420       310650       NaN  
6  2018-05-05T13:34:35.617       207140       NaN  
7  2023-07-07T23:34:22.930       391974       NaN

In [3]:
questions.loc[:, 'Tags'] = questions['Tags'].str.split('|').apply(lambda x: x[1:-1])
questions.head()

Id                                              Title  \
0  437734  Effect of sex at specific point with confidenc...   
1  622877              Poisson process for small sample size   
5  517792  Did I correctly apply the factorisation theore...   
6  344644  IBM SPSS Damped Trend time series analysis met...   
7  620838  Mixed model development for repeated measures ...   

                                                Body  \
0  &lt;p&gt;Assume I model PEFR (related to lung ...   
1  &lt;p&gt;Suppose I have a data set that contai...   
5  &lt;p&gt;Suppose that we have a density &lt;sp...   
6  &lt;p&gt;I have been doing a time series analy...   
7  &lt;p&gt;I have longitudinal data for multiple...   

                                                Tags  PostTypeId  \
0               [r, regression, confidence-interval]           1   
1  [regression, poisson-distribution, poisson-pro...           1   
5  [probability, estimation, inference, estimator...           1   
6                         [time-series, spss, trend]           1   
7  [mixed-model, lme4-nlme, repeated-measures, mu...           1   

              CreationDate  OwnerUserId  ParentId  
0  2019-11-24T19:50:42.807       266724       NaN  
1  2023-08-01T15:57:49.950       314344       NaN  
5  2021-04-01T18:01:50.420       310650       NaN  
6  2018-05-05T13:34:35.617       207140       NaN  
7  2023-07-07T23:34:22.930       391974       NaN

In [4]:
questions_ids = np.concatenate([np.full(count, i) 
                                 for i, count in enumerate(questions['Tags'].apply(len).values)])
all_tags = list(itertools.chain(*(questions['Tags'].values)))

In [5]:
tag_label_encoder1 = LabelEncoder()
all_tag_ids = tag_label_encoder1.fit_transform(all_tags)
all_tag_ids.shape

(652198,)

In [6]:
selected_tags = ['regression', 'hypothesis-testing', 'distributions', 'neural-networks',  'classification', 'clustering']
selected_tag_ids = tag_label_encoder1.transform(selected_tags)

In [7]:
# Select questions with only one of selected_tags
mask = np.isin(all_tag_ids, selected_tag_ids)
print(mask.sum())
questions_with_selected_tags, counts = np.unique(questions_ids[mask], return_counts=True)
questions_with_selected_tags = questions_with_selected_tags[counts==1]
questions_with_selected_tags.shape

67940


(60783,)

In [8]:
mask = np.isin(questions_ids, questions_with_selected_tags)
questions_ids = questions_ids[mask]
all_tag_ids = all_tag_ids[mask]
mask = np.isin(all_tag_ids, selected_tag_ids)
questions_ids = questions_ids[mask]
all_tag_ids = all_tag_ids[mask]

In [9]:
np.unique(all_tag_ids, return_counts=True)

(array([ 185,  193,  386,  635,  973, 1237]),
 array([ 5365,  3541,  8514,  9210,  6904, 27249]))

In [10]:
questions = questions.iloc[questions_ids]
questions['Tag'] = tag_label_encoder1.inverse_transform(all_tag_ids)

print(questions.shape)
questions.head()

(60783, 9)


Id                                              Title  \
0   437734  Effect of sex at specific point with confidenc...   
1   622877              Poisson process for small sample size   
11  178240  linear regression accounting for standard erro...   
14  600361                          Problematic Residual plot   
17  625541          Does skipgram model uses backpropagation?   

                                                 Body  \
0   &lt;p&gt;Assume I model PEFR (related to lung ...   
1   &lt;p&gt;Suppose I have a data set that contai...   
11  &lt;p&gt;I am trying to figure out what is the...   
14  &lt;p&gt;&lt;a href=&quot;https://i.stack.imgu...   
17  &lt;p&gt;I just started to get interested in n...   

                                                 Tags  PostTypeId  \
0                [r, regression, confidence-interval]           1   
1   [regression, poisson-distribution, poisson-pro...           1   
11                  [regression, errors-in-variables]           1   
14                            [regression, residuals]           1   
17  [machine-learning, neural-networks, natural-la...           1   

               CreationDate  OwnerUserId  ParentId              Tag  
0   2019-11-24T19:50:42.807       266724       NaN       regression  
1   2023-08-01T15:57:49.950       314344       NaN       regression  
11  2015-10-22T20:46:44.137        19758       NaN       regression  
14  2022-12-29T16:21:35.377       376392       NaN       regression  
17  2023-08-30T06:56:57.460       302098       NaN  neural-networks

In [11]:
print(questions.shape)
questions.head()

(60783, 9)


Id                                              Title  \
0   437734  Effect of sex at specific point with confidenc...   
1   622877              Poisson process for small sample size   
11  178240  linear regression accounting for standard erro...   
14  600361                          Problematic Residual plot   
17  625541          Does skipgram model uses backpropagation?   

                                                 Body  \
0   &lt;p&gt;Assume I model PEFR (related to lung ...   
1   &lt;p&gt;Suppose I have a data set that contai...   
11  &lt;p&gt;I am trying to figure out what is the...   
14  &lt;p&gt;&lt;a href=&quot;https://i.stack.imgu...   
17  &lt;p&gt;I just started to get interested in n...   

                                                 Tags  PostTypeId  \
0                [r, regression, confidence-interval]           1   
1   [regression, poisson-distribution, poisson-pro...           1   
11                  [regression, errors-in-variables]           1   
14                            [regression, residuals]           1   
17  [machine-learning, neural-networks, natural-la...           1   

               CreationDate  OwnerUserId  ParentId              Tag  
0   2019-11-24T19:50:42.807       266724       NaN       regression  
1   2023-08-01T15:57:49.950       314344       NaN       regression  
11  2015-10-22T20:46:44.137        19758       NaN       regression  
14  2022-12-29T16:21:35.377       376392       NaN       regression  
17  2023-08-30T06:56:57.460       302098       NaN  neural-networks

In [12]:
user_ask_counts = questions['OwnerUserId'].value_counts()
user_ask_counts.head()

OwnerUserId
408603    222
247274    106
28986      99
1005       95
108150     84
Name: count, dtype: int64

In [13]:
user_id_with_counts_gt_1 = user_ask_counts.index[user_ask_counts > 1]
selected_question_idx = []
for idx, owner_user_id in zip(questions.index, questions['OwnerUserId']):
    if owner_user_id in user_id_with_counts_gt_1:
        selected_question_idx.append(idx)
questions = questions.loc[selected_question_idx]
questions.shape

(34153, 9)

In [14]:
questions['Tag'].value_counts()

Tag
regression            15530
hypothesis-testing     4858
distributions          4697
neural-networks        4103
classification         3042
clustering             1923
Name: count, dtype: int64

In [15]:
import re

def clean_text_html(raw_text: str):
    text = re.sub(r'&lt;.*?&gt;', '', raw_text)
    text = text.replace('&#xA;', ' ')
    text = re.sub(r'\s+', ' ', text)
    return text.rstrip()

In [16]:
questions['Body'] = questions['Body'].apply(clean_text_html)

In [17]:
questions.head()

Id                                              Title  \
1   622877              Poisson process for small sample size   
17  625541          Does skipgram model uses backpropagation?   
46  501441  Inference in a system in which (almost) all re...   
50  572092  A faster way of finding unbiased estimators fo...   
73  533957  Would it be wrong if I picked a model with les...   

                                                 Body  \
1   Suppose I have a data set that contains insura...   
17  I just started to get interested in natural la...   
46  We conducted a number of tests on individual s...   
50  No access to computers or calculators is avail...   
73  I have some data containing a list of 2000 que...   

                                                 Tags  PostTypeId  \
1   [regression, poisson-distribution, poisson-pro...           1   
17  [machine-learning, neural-networks, natural-la...           1   
46  [regression, correlation, inference, least-squ...           1   
50  [regression, self-study, multiple-regression, ...           1   
73       [machine-learning, classification, accuracy]           1   

               CreationDate  OwnerUserId  ParentId              Tag  
1   2023-08-01T15:57:49.950       314344       NaN       regression  
17  2023-08-30T06:56:57.460       302098       NaN  neural-networks  
46  2020-12-18T10:53:32.023       107859       NaN       regression  
50  2022-04-19T05:43:00.277       347256       NaN       regression  
73  2021-07-09T11:49:29.693       327301       NaN   classification

In [18]:
questions['Year'] = questions['CreationDate'].apply(lambda x: int(x[:4]))
questions = questions[['Id', 'Title', 'Body', 'Tag', 'Year', 'OwnerUserId', 'Tags']]
questions.reset_index(drop=True, inplace=True)
questions.head()

Id                                              Title  \
0  622877              Poisson process for small sample size   
1  625541          Does skipgram model uses backpropagation?   
2  501441  Inference in a system in which (almost) all re...   
3  572092  A faster way of finding unbiased estimators fo...   
4  533957  Would it be wrong if I picked a model with les...   

                                                Body              Tag  Year  \
0  Suppose I have a data set that contains insura...       regression  2023   
1  I just started to get interested in natural la...  neural-networks  2023   
2  We conducted a number of tests on individual s...       regression  2020   
3  No access to computers or calculators is avail...       regression  2022   
4  I have some data containing a list of 2000 que...   classification  2021   

   OwnerUserId                                               Tags  
0       314344  [regression, poisson-distribution, poisson-pro...  
1       302098  [machine-learning, neural-networks, natural-la...  
2       107859  [regression, correlation, inference, least-squ...  
3       347256  [regression, self-study, multiple-regression, ...  
4       327301       [machine-learning, classification, accuracy]

In [19]:
questions.to_csv('CroVal.csv', index=False)

## Question-User Links

In [20]:
data = {}

In [21]:
question_ids = np.arange(questions.shape[0], dtype=np.uint16)

user_id_encoder = LabelEncoder()
user_ids = user_id_encoder.fit_transform(questions['OwnerUserId'].values).astype(np.uint16)
assert len(user_ids) == len(question_ids)
print('Number of question-user links:', len(question_ids))

data['question-user'] = (question_ids, user_ids)

Number of question-user links: 34153


## Question-Tag Links

In [22]:
question_ids = np.concatenate([np.full(count, i)
                                for i, count in enumerate(questions['Tags'].apply(len).values)])
all_tags = list(itertools.chain(*(questions['Tags'].values)))

In [23]:
tag_label_encoder = LabelEncoder()
all_tag_ids = tag_label_encoder.fit_transform(all_tags)
all_tag_ids.shape

(118712,)

In [24]:
selected_tags = np.unique(questions['Tag'])
selected_tag_ids = tag_label_encoder.transform(selected_tags)

In [25]:
mask = ~np.isin(all_tag_ids, selected_tag_ids)
question_ids = question_ids[mask]
all_tag_ids = all_tag_ids[mask]

tag_label_encoder = LabelEncoder()
all_tag_ids = tag_label_encoder.fit_transform(all_tag_ids)
print('Number of tags:', len(tag_label_encoder.classes_))

print('Number of question-tag links:', len(question_ids))
data['question-tag'] = (question_ids, all_tag_ids)

Number of tags: 1335
Number of question-tag links: 84559


## Question-Question Links

In [26]:
post_links = pd.read_csv('csvs/PostLinks.csv')
post_links.head()

Id             CreationDate  PostId  RelatedPostId  LinkTypeId
0   6140526  2017-02-10T08:09:54.907  261056          82664           1
1  13300159  2020-02-24T03:34:51.287  448097         441156           1
2   3805280  2015-03-04T21:44:24.393  140369         140163           1
3   3953036  2015-04-30T14:11:47.800  149074          35019           1
4  11264471  2018-11-25T16:21:16.053  378611         377444           3

In [27]:
src_post_ids = post_links['PostId'].values
dst_post_ids = post_links['RelatedPostId'].values
mask = (np.isin(src_post_ids, questions['Id'].values) & 
        np.isin(dst_post_ids, questions['Id'].values))
src_post_ids = src_post_ids[mask]
dst_post_ids = dst_post_ids[mask]

In [28]:
post_id_map = dict(zip(questions['Id'].values, range(len(questions))))
src_post_ids = np.array([post_id_map[_] for _ in src_post_ids], dtype=np.uint16)
post_id_map = dict(zip(questions['Id'].values, range(len(questions))))
dst_post_ids = np.array([post_id_map[_] for _ in dst_post_ids], dtype=np.uint16)

In [29]:
print('Number of question-question links:', src_post_ids.shape[0])
data['question-question'] = (src_post_ids, dst_post_ids)

Number of question-question links: 6743


## Labels and Years

In [30]:
question_years = questions['Year'].values.astype(np.int16)

label_encoder = LabelEncoder()
question_labels = label_encoder.fit_transform(questions['Tag']).astype(np.int8)

data['question_years'] = question_years
data['question_labels'] = question_labels

### Node Features

We generate embeddings as features for each node in the graph. Node embeddings are generated by passing the title and body through a Sentence-BERT model and obtaining a 384-embedding vector for each movie node.


According to [Sentence-Transformers docs](https://www.sbert.net/docs/pretrained_models.html), the **all-MiniLM-L6-v2** model provides the best quality. So we use it to generate node features.

all-MiniLM-L6-v2

Description:	All-round model tuned for many use-cases. Trained on a large and diverse dataset of over 1 billion training pairs.
Base Model:	nreimers/MiniLM-L6-H384-uncased
Max Sequence Length:	256
Dimensions:	384
Normalized Embeddings:	true
Suitable Score Functions:	dot-product (util.dot_score), cosine-similarity (util.cos_sim), euclidean distance
Size:	80 MB
Pooling:	Mean Pooling
Training Data:	1B+ training pairs. For details, see model card.
Model Card:	https://huggingface.co/sentence-transformers/all-MiniLM-L6-v2


In [31]:
import torch
from sentence_transformers import SentenceTransformer

device = 'cuda:0' if torch.cuda.is_available() else 'cpu'
model = SentenceTransformer('../sentence-transformers/all-MiniLM-L6-v2', device=device)
model

/usr/local/lib/python3.10/dist-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
)

In [32]:
text = questions['Title'] + ' ' + questions['Body']

In [33]:
feats = model.encode(text, batch_size=4096, show_progress_bar=True, convert_to_numpy=True)

Batches: 100%|██████████| 9/9 [00:31<00:00,  3.49s/it]


In [34]:
data['question_feats'] = feats
data

{'question-user': (array([    0,     1,     2, ..., 34150, 34151, 34152], dtype=uint16),
  array([7927, 7752, 3986, ...,   67, 3988, 4143], dtype=uint16)),
 'question-tag': (array([    0,     0,     0, ..., 34150, 34150, 34152]),
  array([920, 921, 397, ..., 981, 419, 331])),
 'question-question': (array([8581,  678, 5604, ..., 4463, 4463, 4053], dtype=uint16),
  array([11735,  9756, 18156, ..., 19652, 19652, 19002], dtype=uint16)),
 'question_years': array([2023, 2023, 2020, ..., 2010, 2017, 2016], dtype=int16),
 'question_labels': array([5, 4, 5, ..., 2, 5, 4], dtype=int8),
 'question_feats': array([[-0.02393158,  0.06053483,  0.03126719, ..., -0.10800511,
         -0.00546587,  0.03609833],
        [-0.05885282, -0.11182664,  0.02024328, ...,  0.07537424,
          0.05215778, -0.04128488],
        [-0.06636419, -0.0513887 , -0.01564158, ..., -0.00976081,
          0.01578866, -0.04567946],
        ...,
        [-0.12249381, -0.03751755,  0.03033727, ..., -0.03496004,
         -0.04

In [35]:
import pickle

with open('croval.pkl', 'wb') as f:
    pickle.dump(data, f)